In [1]:
import numpy as np
import pandas as pd
import polars as pl
from tqdm import tqdm
from sklearn.metrics import f1_score
from sklearn.model_selection import GroupKFold, KFold
from catboost import CatBoostClassifier, Pool
import matplotlib.pyplot as plt
import warnings
from itertools import combinations
import math

warnings.filterwarnings('ignore')
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", 200)

targets = pd.read_csv('../input/predict-student-performance-from-game-play/train_labels.csv')
targets['session'] = targets.session_id.apply(lambda x: int(x.split('_')[0]))
targets['q'] = targets.session_id.apply(lambda x: int(x.split('_')[-1][1:]))

In [2]:
%%time
df = pl.read_csv('../input/predict-student-performance-from-game-play/train.csv')

Wall time: 6.48 s


In [3]:
columns = [
    pl.col("page").cast(pl.Float32),
    (
        (pl.col("elapsed_time") - pl.col("elapsed_time").shift(1))
        .fill_null(0)
        .clip(0, 1e9)
        .over(["session_id", "level"])
        .alias("elapsed_time_diff")
    ),
    (
        (pl.col("screen_coor_x") - pl.col("screen_coor_x").shift(1))
        .abs()
        .over(["session_id", "level"])
    ),
    (
        (pl.col("screen_coor_y") - pl.col("screen_coor_y").shift(1))
        .abs()
        .over(["session_id", "level"])
    ),
    pl.col("fqid").fill_null("fqid_None"),
    pl.col("text_fqid").fill_null("text_fqid_None"),
    pl.col("text").fill_null("text_None")

]

In [4]:
df = df.with_columns(columns)

In [5]:
test_dict = dict(zip(sorted(list(df['text'].unique())),[f'text_{xx}' for xx in range(len(df['text'].unique()))]))
test_list = sorted(list(df['text'].unique()))

In [6]:
df = df.with_columns(
    pl.col("text").map_dict(test_dict).alias("text_code")
    )

In [7]:
df.head()

shape: (5, 22)
┌───────────────────┬───────┬──────────────┬────────────────┬───┬───────┬─────────────┬───────────────────┬───────────┐
│ session_id        ┆ index ┆ elapsed_time ┆ event_name     ┆ … ┆ music ┆ level_group ┆ elapsed_time_diff ┆ text_code │
│ ---               ┆ ---   ┆ ---          ┆ ---            ┆   ┆ ---   ┆ ---         ┆ ---               ┆ ---       │
│ i64               ┆ i64   ┆ i64          ┆ str            ┆   ┆ i64   ┆ str         ┆ i64               ┆ str       │
╞═══════════════════╪═══════╪══════════════╪════════════════╪═══╪═══════╪═════════════╪═══════════════════╪═══════════╡
│ 20090312431273200 ┆ 0     ┆ 0            ┆ cutscene_click ┆ … ┆ 1     ┆ 0-4         ┆ 0                 ┆ text_597  │
│ 20090312431273200 ┆ 1     ┆ 1323         ┆ person_click   ┆ … ┆ 1     ┆ 0-4         ┆ 1323              ┆ text_517  │
│ 20090312431273200 ┆ 2     ┆ 831          ┆ person_click   ┆ … ┆ 1     ┆ 0-4         ┆ 0                 ┆ text_298  │
│ 20090312431273200 ┆ 3     ┆ 1147         ┆ person_click   ┆ … ┆ 1     ┆ 0-4         ┆ 316               ┆ text_200  │
│ 20090312431273200 ┆ 4     ┆ 1863         ┆ person_click   ┆ … ┆ 1     ┆ 0-4         ┆ 716               ┆ text_43   │
└───────────────────┴───────┴──────────────┴────────────────┴───┴───────┴─────────────┴───────────────────┴───────────┘

In [8]:
df1 = df.filter(pl.col("level_group") == '0-4')
df2 = df.filter(pl.col("level_group") == '5-12')
df3 = df.filter(pl.col("level_group") == '13-22')

In [9]:
CATS = ['event_name', 'name', 'fqid', 'room_fqid', 'text_fqid']
NUMS = ['page', 'room_coor_x', 'room_coor_y', 'screen_coor_x', 'screen_coor_y',
        'hover_duration', 'elapsed_time_diff', 'fullscreen', 'hq', 'music']
fqid_lists = ['worker', 'archivist', 'gramps', 'wells', 'toentry', 'confrontation', 'crane_ranger', 'groupconvo', 'flag_girl', 'tomap', 'tostacks', 'tobasement', 'archivist_glasses', 'boss', 'journals', 'seescratches', 'groupconvo_flag', 'cs', 'teddy', 'expert', 'businesscards', 'ch3start', 'tunic.historicalsociety', 'tofrontdesk', 'savedteddy', 'plaque', 'glasses', 'tunic.drycleaner', 'reader_flag', 'tunic.library', 'tracks', 'tunic.capitol_2', 'trigger_scarf', 'reader', 'directory', 'tunic.capitol_1', 'journals.pic_0.next', 'unlockdoor', 'tunic', 'what_happened', 'tunic.kohlcenter', 'tunic.humanecology', 'colorbook', 'logbook', 'businesscards.card_0.next', 'journals.hub.topics', 'logbook.page.bingo', 'journals.pic_1.next', 'journals_flag', 'reader.paper0.next', 'tracks.hub.deer', 'reader_flag.paper0.next', 'trigger_coffee', 'wellsbadge', 'journals.pic_2.next', 'tomicrofiche', 'journals_flag.pic_0.bingo', 'plaque.face.date', 'notebook', 'tocloset_dirty', 'businesscards.card_bingo.bingo', 'businesscards.card_1.next', 'tunic.wildlife', 'tunic.hub.slip', 'tocage', 'journals.pic_2.bingo', 'tocollectionflag', 'tocollection', 'chap4_finale_c', 'chap2_finale_c', 'lockeddoor', 'journals_flag.hub.topics', 'tunic.capitol_0', 'reader_flag.paper2.bingo', 'photo', 'tunic.flaghouse', 'reader.paper1.next', 'directory.closeup.archivist', 'intro', 'businesscards.card_bingo.next', 'reader.paper2.bingo', 'retirement_letter', 'remove_cup', 'journals_flag.pic_0.next', 'magnify', 'coffee', 'key', 'togrampa', 'reader_flag.paper1.next', 'janitor', 'tohallway', 'chap1_finale', 'report', 'outtolunch', 'journals_flag.hub.topics_old', 'journals_flag.pic_1.next', 'reader.paper2.next', 'chap1_finale_c', 'reader_flag.paper2.next', 'door_block_talk', 'journals_flag.pic_1.bingo', 'journals_flag.pic_2.next', 'journals_flag.pic_2.bingo', 'block_magnify', 'reader.paper0.prev', 'block', 'reader_flag.paper0.prev', 'block_0', 'door_block_clean', 'reader.paper2.prev', 'reader.paper1.prev', 'doorblock', 'tocloset', 'reader_flag.paper2.prev', 'reader_flag.paper1.prev', 'block_tomap2', 'journals_flag.pic_0_old.next', 'journals_flag.pic_1_old.next', 'block_tocollection', 'block_nelson', 'journals_flag.pic_2_old.next', 'block_tomap1', 'block_badge', 'need_glasses', 'block_badge_2', 'fox', 'block_1']
DIALOGS = ['that', 'this', 'it', 'you','find','found','Found','notebook','Wells','wells','help','need', 'Oh','Ooh','Jo', 'flag', 'can','and','is','the','to']

name_feature = ['basic', 'undefined', 'close', 'open', 'prev', 'next']
event_name_feature = ['cutscene_click', 'person_click', 'navigate_click',
       'observation_click', 'notification_click', 'object_click',
       'object_hover', 'map_hover', 'map_click', 'checkpoint',
       'notebook_click']
text_lists = ['tunic.historicalsociety.cage.confrontation', 'tunic.wildlife.center.crane_ranger.crane', 'tunic.historicalsociety.frontdesk.archivist.newspaper', 'tunic.historicalsociety.entry.groupconvo', 'tunic.wildlife.center.wells.nodeer', 'tunic.historicalsociety.frontdesk.archivist.have_glass', 'tunic.drycleaner.frontdesk.worker.hub', 'tunic.historicalsociety.closet_dirty.gramps.news', 'tunic.humanecology.frontdesk.worker.intro', 'tunic.historicalsociety.frontdesk.archivist_glasses.confrontation', 'tunic.historicalsociety.basement.seescratches', 'tunic.historicalsociety.collection.cs', 'tunic.flaghouse.entry.flag_girl.hello', 'tunic.historicalsociety.collection.gramps.found', 'tunic.historicalsociety.basement.ch3start', 'tunic.historicalsociety.entry.groupconvo_flag', 'tunic.library.frontdesk.worker.hello', 'tunic.library.frontdesk.worker.wells', 'tunic.historicalsociety.collection_flag.gramps.flag', 'tunic.historicalsociety.basement.savedteddy', 'tunic.library.frontdesk.worker.nelson', 'tunic.wildlife.center.expert.removed_cup', 'tunic.library.frontdesk.worker.flag', 'tunic.historicalsociety.frontdesk.archivist.hello', 'tunic.historicalsociety.closet.gramps.intro_0_cs_0', 'tunic.historicalsociety.entry.boss.flag', 'tunic.flaghouse.entry.flag_girl.symbol', 'tunic.historicalsociety.closet_dirty.trigger_scarf', 'tunic.drycleaner.frontdesk.worker.done', 'tunic.historicalsociety.closet_dirty.what_happened', 'tunic.wildlife.center.wells.animals', 'tunic.historicalsociety.closet.teddy.intro_0_cs_0', 'tunic.historicalsociety.cage.glasses.afterteddy', 'tunic.historicalsociety.cage.teddy.trapped', 'tunic.historicalsociety.cage.unlockdoor', 'tunic.historicalsociety.stacks.journals.pic_2.bingo', 'tunic.historicalsociety.entry.wells.flag', 'tunic.humanecology.frontdesk.worker.badger', 'tunic.historicalsociety.stacks.journals_flag.pic_0.bingo', 'tunic.historicalsociety.closet.intro', 'tunic.historicalsociety.closet.retirement_letter.hub', 'tunic.historicalsociety.entry.directory.closeup.archivist', 'tunic.historicalsociety.collection.tunic.slip', 'tunic.kohlcenter.halloffame.plaque.face.date', 'tunic.historicalsociety.closet_dirty.trigger_coffee', 'tunic.drycleaner.frontdesk.logbook.page.bingo', 'tunic.library.microfiche.reader.paper2.bingo', 'tunic.kohlcenter.halloffame.togrampa', 'tunic.capitol_2.hall.boss.haveyougotit', 'tunic.wildlife.center.wells.nodeer_recap', 'tunic.historicalsociety.cage.glasses.beforeteddy', 'tunic.historicalsociety.closet_dirty.gramps.helpclean', 'tunic.wildlife.center.expert.recap', 'tunic.historicalsociety.frontdesk.archivist.have_glass_recap', 'tunic.historicalsociety.stacks.journals_flag.pic_1.bingo', 'tunic.historicalsociety.cage.lockeddoor', 'tunic.historicalsociety.stacks.journals_flag.pic_2.bingo', 'tunic.historicalsociety.collection.gramps.lost', 'tunic.historicalsociety.closet.notebook', 'tunic.historicalsociety.frontdesk.magnify', 'tunic.humanecology.frontdesk.businesscards.card_bingo.bingo', 'tunic.wildlife.center.remove_cup', 'tunic.library.frontdesk.wellsbadge.hub', 'tunic.wildlife.center.tracks.hub.deer', 'tunic.historicalsociety.frontdesk.key', 'tunic.library.microfiche.reader_flag.paper2.bingo', 'tunic.flaghouse.entry.colorbook', 'tunic.wildlife.center.coffee', 'tunic.capitol_1.hall.boss.haveyougotit', 'tunic.historicalsociety.basement.janitor', 'tunic.historicalsociety.collection_flag.gramps.recap', 'tunic.wildlife.center.wells.animals2', 'tunic.flaghouse.entry.flag_girl.symbol_recap', 'tunic.historicalsociety.closet_dirty.photo', 'tunic.historicalsociety.stacks.outtolunch', 'tunic.library.frontdesk.worker.wells_recap', 'tunic.historicalsociety.frontdesk.archivist_glasses.confrontation_recap', 'tunic.capitol_0.hall.boss.talktogramps', 'tunic.historicalsociety.closet.photo', 'tunic.historicalsociety.collection.tunic', 'tunic.historicalsociety.closet.teddy.intro_0_cs_5', 'tunic.historicalsociety.closet_dirty.gramps.archivist', 'tunic.historicalsociety.closet_dirty.door_block_talk', 'tunic.historicalsociety.entry.boss.flag_recap', 'tunic.historicalsociety.frontdesk.archivist.need_glass_0', 'tunic.historicalsociety.entry.wells.talktogramps', 'tunic.historicalsociety.frontdesk.block_magnify', 'tunic.historicalsociety.frontdesk.archivist.foundtheodora', 'tunic.historicalsociety.closet_dirty.gramps.nothing', 'tunic.historicalsociety.closet_dirty.door_block_clean', 'tunic.capitol_1.hall.boss.writeitup', 'tunic.library.frontdesk.worker.nelson_recap', 'tunic.library.frontdesk.worker.hello_short', 'tunic.historicalsociety.stacks.block', 'tunic.historicalsociety.frontdesk.archivist.need_glass_1', 'tunic.historicalsociety.entry.boss.talktogramps', 'tunic.historicalsociety.frontdesk.archivist.newspaper_recap', 'tunic.historicalsociety.entry.wells.flag_recap', 'tunic.drycleaner.frontdesk.worker.done2', 'tunic.library.frontdesk.worker.flag_recap', 'tunic.humanecology.frontdesk.block_0', 'tunic.library.frontdesk.worker.preflag', 'tunic.historicalsociety.basement.gramps.seeyalater', 'tunic.flaghouse.entry.flag_girl.hello_recap', 'tunic.historicalsociety.closet.doorblock', 'tunic.drycleaner.frontdesk.worker.takealook', 'tunic.historicalsociety.basement.gramps.whatdo', 'tunic.library.frontdesk.worker.droppedbadge', 'tunic.historicalsociety.entry.block_tomap2', 'tunic.library.frontdesk.block_nelson', 'tunic.library.microfiche.block_0', 'tunic.historicalsociety.entry.block_tocollection', 'tunic.historicalsociety.entry.block_tomap1', 'tunic.historicalsociety.collection.gramps.look_0', 'tunic.library.frontdesk.block_badge', 'tunic.historicalsociety.cage.need_glasses', 'tunic.library.frontdesk.block_badge_2', 'tunic.kohlcenter.halloffame.block_0', 'tunic.capitol_0.hall.chap1_finale_c', 'tunic.capitol_1.hall.chap2_finale_c', 'tunic.capitol_2.hall.chap4_finale_c', 'tunic.wildlife.center.fox.concern', 'tunic.drycleaner.frontdesk.block_0', 'tunic.historicalsociety.entry.gramps.hub', 'tunic.humanecology.frontdesk.block_1', 'tunic.drycleaner.frontdesk.block_1']
room_lists = ['tunic.historicalsociety.entry', 'tunic.wildlife.center', 'tunic.historicalsociety.cage', 'tunic.library.frontdesk', 'tunic.historicalsociety.frontdesk', 'tunic.historicalsociety.stacks', 'tunic.historicalsociety.closet_dirty', 'tunic.humanecology.frontdesk', 'tunic.historicalsociety.basement', 'tunic.kohlcenter.halloffame', 'tunic.library.microfiche', 'tunic.drycleaner.frontdesk', 'tunic.historicalsociety.collection', 'tunic.historicalsociety.closet', 'tunic.flaghouse.entry', 'tunic.historicalsociety.collection_flag', 'tunic.capitol_1.hall', 'tunic.capitol_0.hall', 'tunic.capitol_2.hall']

LEVELS = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22]
level_groups = ["0-4", "5-12", "13-22"]

def feature_engineer(x, grp, use_extra, feature_suffix):
    aggs = [
        pl.col("index").count().alias(f"session_number_{feature_suffix}"),
        
        #text
        *[pl.col('index').filter(pl.col('text').str.contains(c)).count().alias(f'word_{c}') for c in DIALOGS],
        *[pl.col("elapsed_time_diff").filter((pl.col('text').str.contains(c))).mean().alias(f'word_mean_{c}') for c in
          DIALOGS],
        *[pl.col("elapsed_time_diff").filter((pl.col('text').str.contains(c))).std().alias(f'word_std_{c}') for c in
          DIALOGS],
        *[pl.col("elapsed_time_diff").filter((pl.col('text').str.contains(c))).max().alias(f'word_max_{c}') for c in
          DIALOGS],
        *[pl.col("elapsed_time_diff").filter((pl.col('text').str.contains(c))).sum().alias(f'word_sum_{c}') for c in
          DIALOGS],
        *[pl.col("elapsed_time_diff").filter((pl.col('text').str.contains(c))).median().alias(f'word_median_{c}') for c
          in DIALOGS],
        
        *[pl.col('text_code').filter(pl.col('text_code') == c).count().alias(f'{c}_text_code_counts{feature_suffix}') for c in test_list],
        *[pl.col("elapsed_time_diff").filter((pl.col('text_code') == c)).mean().alias(f'{c}_text_mean_{feature_suffix}') for c in
          test_list],
        *[pl.col("elapsed_time_diff").filter((pl.col('text_code') == c)).std().alias(f'{c}_text_std_{feature_suffix}') for c in
          test_list],
        *[pl.col("elapsed_time_diff").filter((pl.col('text_code') == c)).max().alias(f'{c}_text_max_{feature_suffix}') for c in
          test_list],
        *[pl.col("elapsed_time_diff").filter((pl.col('text_code') == c)).sum().alias(f'{c}_text_sum_{feature_suffix}') for c in
          test_list],
        *[pl.col("elapsed_time_diff").filter((pl.col('text_code') == c)).median().alias(f'{c}_text_median_{feature_suffix}') for c
          in test_list],
        
        
        *[pl.col(c).drop_nulls().n_unique().alias(f"{c}_unique_{feature_suffix}") for c in CATS],

        *[pl.col(c).mean().alias(f"{c}_mean_{feature_suffix}") for c in NUMS],
        *[pl.col(c).std().alias(f"{c}_std_{feature_suffix}") for c in NUMS],
        *[pl.col(c).min().alias(f"{c}_min_{feature_suffix}") for c in NUMS],
        *[pl.col(c).max().alias(f"{c}_max_{feature_suffix}") for c in NUMS],
        *[pl.col(c).median().alias(f"{c}_median_{feature_suffix}") for c in NUMS],

        *[pl.col("fqid").filter(pl.col("fqid") == c).count().alias(f"{c}_fqid_counts{feature_suffix}")
          for c in fqid_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("fqid") == c).std().alias(f"{c}_ET_std_{feature_suffix}") for
          c in fqid_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("fqid") == c).mean().alias(f"{c}_ET_mean_{feature_suffix}") for
          c in fqid_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("fqid") == c).sum().alias(f"{c}_ET_sum_{feature_suffix}") for
          c in fqid_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("fqid") == c).median().alias(f"{c}_ET_median_{feature_suffix}") for
          c in fqid_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("fqid") == c).max().alias(f"{c}_ET_max_{feature_suffix}") for
          c in fqid_lists],

        *[pl.col("text_fqid").filter(pl.col("text_fqid") == c).count().alias(f"{c}_text_fqid_counts{feature_suffix}")
          for
          c in text_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("text_fqid") == c).std().alias(f"{c}_ET_std_{feature_suffix}") for
          c in text_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("text_fqid") == c).mean().alias(f"{c}_ET_mean_{feature_suffix}") for
          c in text_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("text_fqid") == c).sum().alias(f"{c}_ET_sum_{feature_suffix}") for
          c in text_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("text_fqid") == c).median().alias(f"{c}_ET_median_{feature_suffix}")
          for
          c in text_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("text_fqid") == c).max().alias(f"{c}_ET_max_{feature_suffix}") for
          c in text_lists],

        *[pl.col("room_fqid").filter(pl.col("room_fqid") == c).count().alias(f"{c}_room_fqid_counts{feature_suffix}")
          for c in room_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("room_fqid") == c).std().alias(f"{c}_ET_std_{feature_suffix}") for
          c in room_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("room_fqid") == c).mean().alias(f"{c}_ET_mean_{feature_suffix}") for
          c in room_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("room_fqid") == c).sum().alias(f"{c}_ET_sum_{feature_suffix}") for
          c in room_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("room_fqid") == c).median().alias(f"{c}_ET_median_{feature_suffix}")
          for
          c in room_lists],
        *[pl.col("elapsed_time_diff").filter(pl.col("room_fqid") == c).max().alias(f"{c}_ET_max_{feature_suffix}") for
          c in room_lists],

        *[pl.col("event_name").filter(pl.col("event_name") == c).count().alias(f"{c}_event_name_counts{feature_suffix}")
          for c in event_name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("event_name") == c).std().alias(f"{c}_ET_std_{feature_suffix}") for
          c in event_name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("event_name") == c).mean().alias(f"{c}_ET_mean_{feature_suffix}")
          for
          c in event_name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("event_name") == c).sum().alias(f"{c}_ET_sum_{feature_suffix}") for
          c in event_name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("event_name") == c).median().alias(
            f"{c}_ET_median_{feature_suffix}") for
          c in event_name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("event_name") == c).max().alias(f"{c}_ET_max_{feature_suffix}") for
          c in event_name_feature],

        *[pl.col("name").filter(pl.col("name") == c).count().alias(f"{c}_name_counts{feature_suffix}") for c in
          name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("name") == c).std().alias(f"{c}_ET_std_{feature_suffix}") for c in
          name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("name") == c).mean().alias(f"{c}_ET_mean_{feature_suffix}") for c in
          name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("name") == c).sum().alias(f"{c}_ET_sum_{feature_suffix}") for c in
          name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("name") == c).median().alias(f"{c}_ET_median_{feature_suffix}") for
          c in
          name_feature],
        *[pl.col("elapsed_time_diff").filter(pl.col("name") == c).max().alias(f"{c}_ET_max_{feature_suffix}") for c in
          name_feature],

        *[pl.col("level").filter(pl.col("level") == c).count().alias(f"{c}_LEVEL_count{feature_suffix}") for c in
          LEVELS],
        *[pl.col("elapsed_time_diff").filter(pl.col("level") == c).std().alias(f"{c}_ET_std_{feature_suffix}") for c in
          LEVELS],
        *[pl.col("elapsed_time_diff").filter(pl.col("level") == c).mean().alias(f"{c}_ET_mean_{feature_suffix}") for c
          in
          LEVELS],
        *[pl.col("elapsed_time_diff").filter(pl.col("level") == c).sum().alias(f"{c}_ET_sum_{feature_suffix}") for c in
          LEVELS],
        *[pl.col("elapsed_time_diff").filter(pl.col("level") == c).median().alias(f"{c}_ET_median_{feature_suffix}") for
          c in
          LEVELS],
        *[pl.col("elapsed_time_diff").filter(pl.col("level") == c).max().alias(f"{c}_ET_max_{feature_suffix}") for c in
          LEVELS],

        *[pl.col("level_group").filter(pl.col("level_group") == c).count().alias(
            f"{c}_LEVEL_group_count{feature_suffix}") for c in
          level_groups],
        *[pl.col("elapsed_time_diff").filter(pl.col("level_group") == c).std().alias(f"{c}_ET_std_{feature_suffix}") for
          c in
          level_groups],
        *[pl.col("elapsed_time_diff").filter(pl.col("level_group") == c).mean().alias(f"{c}_ET_mean_{feature_suffix}")
          for c in
          level_groups],
        *[pl.col("elapsed_time_diff").filter(pl.col("level_group") == c).sum().alias(f"{c}_ET_sum_{feature_suffix}") for
          c in
          level_groups],
        *[pl.col("elapsed_time_diff").filter(pl.col("level_group") == c).median().alias(
            f"{c}_ET_median_{feature_suffix}") for c in
          level_groups],
        *[pl.col("elapsed_time_diff").filter(pl.col("level_group") == c).max().alias(f"{c}_ET_max_{feature_suffix}") for
          c in
          level_groups],

    ]

    df = x.groupby(['session_id'], maintain_order=True).agg(aggs).sort("session_id")

    if use_extra:
        if grp == '5-12':
            aggs = [
                pl.col("elapsed_time").filter((pl.col("text") == "Here's the log book.")
                                              | (pl.col("fqid") == 'logbook.page.bingo'))
                    .apply(lambda s: s.max() - s.min()).alias("logbook_bingo_duration"),
                pl.col("index").filter(
                    (pl.col("text") == "Here's the log book.") | (pl.col("fqid") == 'logbook.page.bingo')).apply(
                    lambda s: s.max() - s.min()).alias("logbook_bingo_indexCount"),
                pl.col("elapsed_time").filter(
                    ((pl.col("event_name") == 'navigate_click') & (pl.col("fqid") == 'reader')) | (
                            pl.col("fqid") == "reader.paper2.bingo")).apply(lambda s: s.max() - s.min()).alias(
                    "reader_bingo_duration"),
                pl.col("index").filter(((pl.col("event_name") == 'navigate_click') & (pl.col("fqid") == 'reader')) | (
                        pl.col("fqid") == "reader.paper2.bingo")).apply(lambda s: s.max() - s.min()).alias(
                    "reader_bingo_indexCount"),
                pl.col("elapsed_time").filter(
                    ((pl.col("event_name") == 'navigate_click') & (pl.col("fqid") == 'journals')) | (
                            pl.col("fqid") == "journals.pic_2.bingo")).apply(lambda s: s.max() - s.min()).alias(
                    "journals_bingo_duration"),
                pl.col("index").filter(((pl.col("event_name") == 'navigate_click') & (pl.col("fqid") == 'journals')) | (
                        pl.col("fqid") == "journals.pic_2.bingo")).apply(lambda s: s.max() - s.min()).alias(
                    "journals_bingo_indexCount"),
            ]
            tmp = x.groupby(["session_id"], maintain_order=True).agg(aggs).sort("session_id")
            df = df.join(tmp, on="session_id", how='left')

        if grp == '13-22':
            aggs = [
                pl.col("elapsed_time").filter(
                    ((pl.col("event_name") == 'navigate_click') & (pl.col("fqid") == 'reader_flag')) | (
                            pl.col("fqid") == "tunic.library.microfiche.reader_flag.paper2.bingo")).apply(
                    lambda s: s.max() - s.min() if s.len() > 0 else 0).alias("reader_flag_duration"),
                pl.col("index").filter(
                    ((pl.col("event_name") == 'navigate_click') & (pl.col("fqid") == 'reader_flag')) | (
                            pl.col("fqid") == "tunic.library.microfiche.reader_flag.paper2.bingo")).apply(
                    lambda s: s.max() - s.min() if s.len() > 0 else 0).alias("reader_flag_indexCount"),
                pl.col("elapsed_time").filter(
                    ((pl.col("event_name") == 'navigate_click') & (pl.col("fqid") == 'journals_flag')) | (
                            pl.col("fqid") == "journals_flag.pic_0.bingo")).apply(
                    lambda s: s.max() - s.min() if s.len() > 0 else 0).alias("journalsFlag_bingo_duration"),
                pl.col("index").filter(
                    ((pl.col("event_name") == 'navigate_click') & (pl.col("fqid") == 'journals_flag')) | (
                            pl.col("fqid") == "journals_flag.pic_0.bingo")).apply(
                    lambda s: s.max() - s.min() if s.len() > 0 else 0).alias("journalsFlag_bingo_indexCount")
            ]
            tmp = x.groupby(["session_id"], maintain_order=True).agg(aggs).sort("session_id")
            df = df.join(tmp, on="session_id", how='left')

    return df.to_pandas()

df1 = feature_engineer(df1, grp='0-4', use_extra=True, feature_suffix='')
df2 = feature_engineer(df2, grp='5-12', use_extra=True, feature_suffix='')
df3 = feature_engineer(df3, grp='13-22', use_extra=True, feature_suffix='')

def time_feature(train):
    train["year"] = train["session_id"].apply(lambda x: int(str(x)[:2])).astype(np.uint8)
    train["month"] = train["session_id"].apply(lambda x: int(str(x)[2:4])+1).astype(np.uint8)
    train["day"] = train["session_id"].apply(lambda x: int(str(x)[4:6])).astype(np.uint8)
    train["hour"] = train["session_id"].apply(lambda x: int(str(x)[6:8])).astype(np.uint8)
    train["minute"] = train["session_id"].apply(lambda x: int(str(x)[8:10])).astype(np.uint8)
    train["second"] = train["session_id"].apply(lambda x: int(str(x)[10:12])).astype(np.uint8)
    return train

df1 = time_feature(df1)
df2 = time_feature(df2)
df3 = time_feature(df3)

df1 = df1.set_index('session_id')
df2 = df2.set_index('session_id')
df3 = df3.set_index('session_id')

In [10]:
df1

session_number_  word_that  word_this  word_it  word_you  \
session_id                                                                    
20090312431273200              165          4          2       12        11   
20090312433251036              139          4          2       10         9   
20090312455206810              149          3          3       11        10   
20090313091715820              176          4          2       11        12   
20090313571836404              112          4          2       10         9   
...                            ...        ...        ...      ...       ...   
22100215342220508              150          3          3       13        12   
22100215460321130              149          4          3       13        13   
22100217104993650              197          5          2       12        13   
22100219442786200              167          4          2       10         9   
22100221145014656              211          4          3       14        18   

                   word_find  word_found  word_Found  word_notebook  \
session_id                                                            
20090312431273200          1           0           1              3   
20090312433251036          1           0           1              3   
20090312455206810          1           0           1              3   
20090313091715820          2           0           1              3   
20090313571836404          1           0           1              3   
...                      ...         ...         ...            ...   
22100215342220508          1           0           1              3   
22100215460321130          2           0           1              3   
22100217104993650          1           0           1              3   
22100219442786200          1           0           1              3   
22100221145014656          2           0           1              3   

                   word_Wells  word_wells  word_help  word_need  word_Oh  \
session_id                                                                 
20090312431273200           2           0          2          3        0   
20090312433251036           2           0          2          3        0   
20090312455206810           2           0          2          3        0   
20090313091715820           2           0          2          3        0   
20090313571836404           2           0          2          3        0   
...                       ...         ...        ...        ...      ...   
22100215342220508           2           0          2          3        0   
22100215460321130           2           0          2          3        0   
22100217104993650           2           0          2          3        0   
22100219442786200           2           0          2          3        0   
22100221145014656           2           0          2          3        0   

                   word_Ooh  word_Jo  word_flag  word_can  word_and  word_is  \
session_id                                                                     
20090312431273200         0        3          0         1         4       15   
20090312433251036         0        5          0         0         3       13   
20090312455206810         0        3          0         2         5       18   
20090313091715820         0        5          0         2         3       15   
20090313571836404         0        3          0         1         3       14   
...                     ...      ...        ...       ...       ...      ...   
22100215342220508         0        2          0         2         6       20   
22100215460321130         1        2          0         2         5       19   
22100217104993650         1        3          0         3         3       18   
22100219442786200         0        5          0         1         4       14   
22100221145014656         1        2          0         4         8       19   

                   word_the  word_to 

In [11]:
df1.to_pickle('df1.pkl')
df2.to_pickle('df2.pkl')
df3.to_pickle('df3.pkl')

In [6]:
import pickle
f_save = open('textmeta.pkl', 'wb')
pickle.dump([test_list,test_dict], f_save)
f_save.close()

In [14]:
null1 = df1.isnull().sum().sort_values(ascending=False)/len(df1)
null2 = df2.isnull().sum().sort_values(ascending=False)/len(df2)
null3 = df3.isnull().sum().sort_values(ascending=False)/len(df3)

drop1 = list(null1[null1 > 0.99].index)
drop2 = list(null2[null2 > 0.99].index)
drop3 = list(null3[null3 > 0.99].index)

print(len(drop1), len(drop2), len(drop3))

for col in tqdm(df1.columns):
    if df1[col].nunique() == 1:
        print(col)
        drop1.append(col)
for col in tqdm(df2.columns):
    if df2[col].nunique() == 1:
        print(col)
        drop2.append(col)
for col in tqdm(df3.columns):
    if df3[col].nunique() == 1:
        print(col)
        drop3.append(col)

4130 3850 3630


  7%|█████▋                                                                       | 417/5660 [00:00<00:01, 4164.85it/s]

word_found
word_wells
word_Oh
word_flag
*COUGH COUGH COUGH*_text_code_counts
*cough cough*_text_code_counts
*grumble grumble*_text_code_counts
A boring old shirt._text_code_counts
A little horse!_text_code_counts
A real, live ferret!_text_code_counts
A vexy-wha?_text_code_counts
AND I know who took Teddy!_text_code_counts
AND he stole Teddy!_text_code_counts
Actually, I went to school with somebody who LOVES old flags._text_code_counts
Actually, badgers aren't rodents-_text_code_counts
Actually, he's a badger._text_code_counts
Actually, we're just here for some photos._text_code_counts
Ah, Jolie! I'm glad you're here._text_code_counts
Ah, that's better!_text_code_counts
Aha! Good catch, Jo._text_code_counts
Alright, Jolie. Back to work._text_code_counts
An old shirt? Try the university._text_code_counts
And I'll figure out the shirt, too._text_code_counts
And he messed up Gramps's office, too!_text_code_counts
And how did that badger get free?_text_code_counts
And look! She's wearing t

 75%|████████████████████████████████████████████████████████▋                   | 4218/5660 [00:01<00:00, 3645.46it/s]

fullscreen_std_
hq_std_
music_std_
elapsed_time_diff_min_
worker_fqid_counts
archivist_fqid_counts
confrontation_fqid_counts
crane_ranger_fqid_counts
flag_girl_fqid_counts
archivist_glasses_fqid_counts
journals_fqid_counts
seescratches_fqid_counts
groupconvo_flag_fqid_counts
expert_fqid_counts
businesscards_fqid_counts
ch3start_fqid_counts
tofrontdesk_fqid_counts
savedteddy_fqid_counts
glasses_fqid_counts
tunic.drycleaner_fqid_counts
reader_flag_fqid_counts
tunic.library_fqid_counts
tracks_fqid_counts
tunic.capitol_2_fqid_counts
trigger_scarf_fqid_counts
reader_fqid_counts
tunic.capitol_1_fqid_counts
journals.pic_0.next_fqid_counts
unlockdoor_fqid_counts
what_happened_fqid_counts
tunic.humanecology_fqid_counts
colorbook_fqid_counts
logbook_fqid_counts
businesscards.card_0.next_fqid_counts
journals.hub.topics_fqid_counts
logbook.page.bingo_fqid_counts
journals.pic_1.next_fqid_counts
journals_flag_fqid_counts
reader.paper0.next_fqid_counts
tracks.hub.deer_fqid_counts
reader_flag.paper0.n

...

fullscreen_std_
hq_std_
music_std_
elapsed_time_diff_min_
archivist_fqid_counts
groupconvo_fqid_counts
cs_fqid_counts
trigger_scarf_fqid_counts
what_happened_fqid_counts
logbook.page.bingo_fqid_counts
trigger_coffee_fqid_counts
wellsbadge_fqid_counts
plaque.face.date_fqid_counts
notebook_fqid_counts
businesscards.card_bingo.bingo_fqid_counts
chap2_finale_c_fqid_counts
tunic.capitol_0_fqid_counts
intro_fqid_counts
reader.paper2.bingo_fqid_counts
retirement_letter_fqid_counts
magnify_fqid_counts
togrampa_fqid_counts
janitor_fqid_counts
chap1_finale_fqid_counts
report_fqid_counts
chap1_finale_c_fqid_counts
door_block_talk_fqid_counts
block_magnify_fqid_counts
block_fqid_counts
block_0_fqid_counts
door_block_clean_fqid_counts
doorblock_fqid_counts
tocloset_fqid_counts
block_tomap2_fqid_counts
block_tocollection_fqid_counts
block_tomap1_fqid_counts
block_badge_fqid_counts
block_badge_2_fqid_counts
block_1_fqid_counts


 85%|████████████████████████████████████████████████████████████████▊           | 4826/5664 [00:01<00:00, 3173.34it/s]

tunic.historicalsociety.frontdesk.archivist.newspaper_text_fqid_counts
tunic.historicalsociety.entry.groupconvo_text_fqid_counts
tunic.historicalsociety.frontdesk.archivist.have_glass_text_fqid_counts
tunic.drycleaner.frontdesk.worker.hub_text_fqid_counts
tunic.historicalsociety.closet_dirty.gramps.news_text_fqid_counts
tunic.humanecology.frontdesk.worker.intro_text_fqid_counts
tunic.historicalsociety.collection.cs_text_fqid_counts
tunic.historicalsociety.collection.gramps.found_text_fqid_counts
tunic.library.frontdesk.worker.hello_text_fqid_counts
tunic.library.frontdesk.worker.wells_text_fqid_counts
tunic.historicalsociety.frontdesk.archivist.hello_text_fqid_counts
tunic.historicalsociety.closet.gramps.intro_0_cs_0_text_fqid_counts
tunic.historicalsociety.closet_dirty.trigger_scarf_text_fqid_counts
tunic.drycleaner.frontdesk.worker.done_text_fqid_counts
tunic.historicalsociety.closet_dirty.what_happened_text_fqid_counts
tunic.historicalsociety.closet.teddy.intro_0_cs_0_text_fqid_coun

100%|████████████████████████████████████████████████████████████████████████████| 5664/5664 [00:01<00:00, 3457.88it/s]

tunic.historicalsociety.closet_room_fqid_counts
tunic.capitol_0.hall_room_fqid_counts
1_LEVEL_count
2_LEVEL_count
3_LEVEL_count
4_LEVEL_count
5_LEVEL_count
6_LEVEL_count
7_LEVEL_count
8_LEVEL_count
9_LEVEL_count
10_LEVEL_count
11_LEVEL_count
12_LEVEL_count
0-4_LEVEL_group_count
5-12_LEVEL_group_count


In [15]:


FEATURES1 = [c for c in df1.columns if c not in drop1+['level_group']]
FEATURES2 = [c for c in df2.columns if c not in drop2+['level_group']]
FEATURES3 = [c for c in df3.columns if c not in drop3+['level_group']]




print('We will train with', len(FEATURES1), len(FEATURES2), len(FEATURES3), 'features')
ALL_USERS = df1.index.unique()
print('We will train with', len(ALL_USERS), 'users info')

We will train with 701 1047 1309 features
We will train with 23562 users info


In [31]:
def get_feature_importances(data,train_features,q, shuffle, seed=None):
    # Gather real features
    # Go over fold and keep track of CV score (train and valid) and feature importances
    
    # Shuffle target if required
    y = targets.loc[targets.q == q]['correct']

    if shuffle:
        # Here you could as well use a binomial distribution
        y = y.sample(frac=1.0)
    # Fit LightGBM in RF mode, yes it's quicker than sklearn RandomForest
    dtrain = lgb.Dataset(data[train_features], y, free_raw_data=False, silent=True)
    lgb_params = {
        'objective': 'regression',
        'boosting_type': 'gbdt',
        'subsample': 0.8,
        'colsample_bytree': 0.8,
        'num_leaves': 127,
        'max_depth': 7,
        'seed': 42,
        'bagging_freq': 1,
        'n_jobs': 4,
        'verbose': -1
    }
    
    # Fit the model
    clf = lgb.train(params=lgb_params, train_set=dtrain, num_boost_round=200)

    # Get feature importances
    imp_df = pd.DataFrame()
    imp_df["feature"] = list(train_features)
    imp_df["importance_gain"] = clf.feature_importance(importance_type='gain')
    imp_df["importance_split"] = clf.feature_importance(importance_type='split')
    
    return imp_df

In [32]:
def display_distributions(actual_imp_df_, null_imp_df_, feature_):
    plt.figure(figsize=(13, 6))
    gs = gridspec.GridSpec(1, 2)
    # Plot Split importances
    ax = plt.subplot(gs[0, 0])
    a = ax.hist(null_imp_df_.loc[null_imp_df_['feature'] == feature_, 'importance_split'].values, label='Null importances')
    ax.vlines(x=actual_imp_df_.loc[actual_imp_df_['feature'] == feature_, 'importance_split'].mean(), 
               ymin=0, ymax=np.max(a[0]), color='r',linewidth=10, label='Real Target')
    ax.legend()
    ax.set_title('Split Importance of %s' % feature_.upper(), fontweight='bold')
    plt.xlabel('Null Importance (split) Distribution for %s ' % feature_.upper())
    # Plot Gain importances
    ax = plt.subplot(gs[0, 1])
    a = ax.hist(null_imp_df_.loc[null_imp_df_['feature'] == feature_, 'importance_gain'].values, label='Null importances')
    ax.vlines(x=actual_imp_df_.loc[actual_imp_df_['feature'] == feature_, 'importance_gain'].mean(), 
               ymin=0, ymax=np.max(a[0]), color='r',linewidth=10, label='Real Target')
    ax.legend()
    ax.set_title('Gain Importance of %s' % feature_.upper(), fontweight='bold')
    plt.xlabel('Null Importance (gain) Distribution for %s ' % feature_.upper())

In [33]:
# Seed the unexpected randomness of this world
# Get the actual importance, i.e. without shuffling
import lightgbm as lgb
correlation_scores_dict = {}
for q in tqdm(range(1,19)):
    np.random.seed(42)
    if q <= 3:
        grp = '0-4'
        df = df1
        FEATURES = FEATURES1
    elif q <= 13:
        grp = '5-12'
        df = df2
        FEATURES = FEATURES2
    elif q <= 22:
        grp = '13-22'
        df = df3
        FEATURES = FEATURES3
        
    actual_imp_df = get_feature_importances(data=df,train_features=FEATURES,q=q, shuffle=False)
    null_imp_df = pd.DataFrame()
    nb_runs = 30
    import time
    start = time.time()
    dsp = ''
    for i in range(nb_runs):
        # Get current run importances
        imp_df = get_feature_importances(data=df,train_features=FEATURES,q=q, shuffle=True)
        imp_df['run'] = i + 1 
        # Concat the latest importances with the old ones
        null_imp_df = pd.concat([null_imp_df, imp_df], axis=0)
        # Erase previous message
        for l in range(len(dsp)):
            print('\b', end='', flush=True)
        # Display current run and time used
        spent = (time.time() - start) / 60
        dsp = 'Done with %4d of %4d (Spent %5.1f min)' % (i + 1, nb_runs, spent)
        print(dsp, end='', flush=True)
    correlation_scores = []
    for _f in actual_imp_df['feature'].unique():
        f_null_imps = null_imp_df.loc[null_imp_df['feature'] == _f, 'importance_gain'].values
        f_act_imps = actual_imp_df.loc[actual_imp_df['feature'] == _f, 'importance_gain'].values
        gain_score = 100 * (f_null_imps < np.percentile(f_act_imps, 25)).sum() / f_null_imps.size
        f_null_imps = null_imp_df.loc[null_imp_df['feature'] == _f, 'importance_split'].values
        f_act_imps = actual_imp_df.loc[actual_imp_df['feature'] == _f, 'importance_split'].values
        split_score = 100 * (f_null_imps < np.percentile(f_act_imps, 25)).sum() / f_null_imps.size
        correlation_scores.append((_f, split_score, gain_score))
    correlation_scores_dict[q] = correlation_scores
    

  0%|                                                                                           | 0/18 [00:00<?, ?it/s]

Done with   30 of   30 (Spent   3.3 min)

  6%|████▌                                                                             | 1/18 [03:24<57:59, 204.66s/it]

Done with   30 of   30 (Spent   2.7 min)

 11%|█████████                                                                         | 2/18 [06:12<48:51, 183.24s/it]

...

 89%|██████████████████████████████████████████████████████████████████████▏        | 16/18 [1:22:22<12:37, 378.57s/it]

Done with   30 of   30 (Spent   6.6 min)

 94%|██████████████████████████████████████████████████████████████████████████▌    | 17/18 [1:29:18<06:29, 389.59s/it]

Done with   30 of   30 (Spent   5.6 min)

100%|███████████████████████████████████████████████████████████████████████████████| 18/18 [1:35:10<00:00, 317.23s/it]


In [34]:
import pickle
f_save = open('correlation_scores_dict.pkl', 'wb')
pickle.dump(correlation_scores_dict, f_save)
f_save.close()


In [35]:
correlation_scores_dict

{1: [('session_number_', 30.0, 16.666666666666668),
  ('word_that', 33.333333333333336, 76.66666666666667),
  ('word_this', 63.333333333333336, 80.0),
  ('word_it', 73.33333333333333, 60.0),
  ('word_you', 6.666666666666667, 3.3333333333333335),
  ('word_find', 0.0, 0.0),
  ('word_Found', 0.0, 0.0),
  ('word_notebook', 0.0, 0.0),
  ('word_Wells', 0.0, 0.0),
  ('word_help', 0.0, 0.0),
  ('word_need', 0.0, 0.0),
  ('word_Ooh', 0.0, 0.0),
  ('word_Jo', 90.0, 100.0),
  ('word_can', 23.333333333333332, 50.0),
  ('word_and', 23.333333333333332, 46.666666666666664),
  ('word_is', 90.0, 83.33333333333333),
  ('word_the', 76.66666666666667, 76.66666666666667),
  ('word_to', 90.0, 93.33333333333333),
  ('word_mean_that', 36.666666666666664, 26.666666666666668),
  ('word_mean_this', 100.0, 80.0),
  ('word_mean_it', 93.33333333333333, 100.0),
  ('word_mean_you', 36.666666666666664, 26.666666666666668),
  ('word_mean_find', 100.0, 100.0),
  ('word_mean_Found', 70.0, 20.0),
  ('word_mean_notebook', 